# random test 20%

In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
import json

def prepare_data_from_dataframe(df: pd.DataFrame, output_file: str) -> str:
    """Prepare data for finetuning by reading from a DataFrame."""
    data = []

    # Process data
    for _, row in df.iterrows():
        image_path = f"../data/{row['max_key']}/{row['path'].split('/')[-1]}"
        data.append({"image": image_path, "caption": row['max_key']})

    # Save the data in JSON format
    with open(output_file, "w") as f:
        for item in data:
            json.dump(item, f)
            f.write("\n")

    return output_file


# Load the CSV file
df = pd.read_csv('labels.csv')
# Filter out specific categories
df = df[df['max_key'] != 'error']
df = df[df['max_key'] != 'a photo of other indoor space: not kitchen, not bathroom, not living room, not dining room, not foyer']
df = df[df['max_key'] != 'it is a artificial photo']
df = df[df['max_key'] != 'a photo of outdoor space']
# Filter samples with max_value > 0.9
threshold_df = df[df['max_value'] > 0.9]

# Split data into train and test sets
train_df, test_df = train_test_split(threshold_df, test_size=0.2, random_state=42)

# Now use the train_df to prepare your training data
train_all_json = prepare_data_from_dataframe(train_df, 'train_random.json')
# And test_df to prepare your testing data
test_json = prepare_data_from_dataframe(test_df, 'val_random.json')

# The function prepare_data_from_dataframe remains unchanged


In [1]:
# test from org ckpt
import pandas as pd
from collections import Counter
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

def calculate_category_accuracy(true_labels, predicted_labels):
    """Calculate the accuracy for each category and return it as a dictionary."""
    accuracies = {}
    true_labels_counter = Counter(true_labels)
    correct_predictions_counter = Counter([true for true, pred in zip(true_labels, predicted_labels) if true == pred])
    
    for label in true_labels_counter:
        accuracy = (correct_predictions_counter[label] / true_labels_counter[label]) if label in correct_predictions_counter else 0
        accuracies[label] = accuracy
    
    return accuracies

# Load the JSON data
with open('val_random.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 128  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"


image_processor = AutoImageProcessor.from_pretrained(repo_id)
tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
model = AutoModel.from_pretrained(repo_id)
clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                         device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(repo_id))

all_predictions = []
all_true_labels = []

for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
    batch_images = []
    valid_labels = []
    for path, label in zip(batch_paths, batch_labels):
        try:
            batch_images.append(Image.open(path))
            valid_labels.append(label)
        except (FileNotFoundError, UnidentifiedImageError):
            continue  # Skip images that cannot be opened

    # Get predictions for the batch of images
    predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
    predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

    all_predictions.extend(predicted_labels)
    all_true_labels.extend(valid_labels)

correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
accuracy = correct_predictions / len(all_true_labels)
print(f"Accuracy for model org: {accuracy * 100:.2f}%\n")

# Calculate the accuracy for each category
category_accuracies = calculate_category_accuracy(all_true_labels, all_predictions)

# Print the accuracy for each category
print("Accuracy for each category:")
for category, accuracy in category_accuracies.items():
    print(f"{category}: {accuracy:.2f}")

# Convert the dictionary to a DataFrame
category_accuracy_df = pd.DataFrame(list(category_accuracies.items()), columns=['Category', 'Accuracy'])

# Save the DataFrame to a CSV file
category_accuracy_df.to_csv('category_accuracy.csv', index=False)

Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.

KeyboardInterrupt



In [ ]:
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
unique_labels = list(set(all_true_labels))
# Compute the confusion matrix
cm = confusion_matrix(all_true_labels, all_predictions, labels=unique_labels)

# Display the confusion matrix
fig, ax = plt.subplots(figsize=(10, 10))  # Adjust the size as needed
disp = ConfusionMatrixDisplay(confusion_matrix=cm, display_labels=unique_labels)
disp.plot(ax=ax)

# Rotate the x-axis labels to display them vertically
plt.xticks(rotation=90)

plt.show()

In [2]:
import pandas as pd
from sklearn.model_selection import KFold
import json

def prepare_data_from_dataframe(df, output_file):
    """Prepare data for fine-tuning by reading from a DataFrame."""
    data = []
    # Process data
    for _, row in df.iterrows():
        image_path = f"../data/{row['max_key']}/{row['path'].split('/')[-1]}"
        data.append({"image": image_path, "caption": row['max_key']})
    # Save the data in JSON format
    with open(output_file, "w") as f:
        for item in data:
            json.dump(item, f)
            f.write("\n")

def perform_k_fold(df, n_splits):
    """Perform K-fold split and data preparation, including filtering by confidence thresholds."""
    kf = KFold(n_splits=n_splits, shuffle=True, random_state=42)
    fold_data_info = []
    fold_counter = 0

    for train_index, test_index in kf.split(df):
        train_df, test_df = df.iloc[train_index], df.iloc[test_index]
        test_json = f'val_fold_{fold_counter}.json'
        prepare_data_from_dataframe(test_df, test_json)
        
        # Creating JSON files for each confidence threshold from 0.91 to 0.99
        for threshold in range(90, 100):
            threshold_df = train_df[train_df['max_value'] > threshold / 100.0]
            threshold_train_json = f'train_fold_{fold_counter}_thr_{threshold}.json'
            prepare_data_from_dataframe(threshold_df, threshold_train_json)
            fold_data_info.append((threshold_train_json, test_json))
        
        fold_counter += 1

    return fold_data_info

# Load and preprocess the DataFrame
df = pd.read_csv('labels.csv')
df = df[df['max_key'] != 'error']
df = df[df['max_key'] != 'a photo of other indoor space: not kitchen, not bathroom, not living room, not dining room, not foyer']
df = df[df['max_key'] != 'it is a artificial photo']
df = df[df['max_key'] != 'a photo of outdoor space']
df = df[df['max_value'] > 0.9]

# Perform the 5-fold split and data preparation including threshold filtering
fold_files = perform_k_fold(df, 5)

# Print out the file names for each fold and threshold
for train_file, test_file in fold_files:
    print(f"Train file for this fold and threshold: {train_file}")
    print(f"Test file for this fold: {test_file}")

Train file for this fold: train_fold_0.json
Test file for this fold: val_fold_0.json
Train file for this fold: train_fold_1.json
Test file for this fold: val_fold_1.json
Train file for this fold: train_fold_2.json
Test file for this fold: val_fold_2.json
Train file for this fold: train_fold_3.json
Test file for this fold: val_fold_3.json
Train file for this fold: train_fold_4.json
Test file for this fold: val_fold_4.json


In [11]:
# test from org ckpt
import pandas as pd
import numpy as np
from collections import Counter
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

def calculate_category_accuracy(true_labels, predicted_labels):
    """Calculate the accuracy for each category and return it as a dictionary."""
    accuracies = {}
    true_labels_counter = Counter(true_labels)
    correct_predictions_counter = Counter([true for true, pred in zip(true_labels, predicted_labels) if true == pred])
    
    for label in true_labels_counter:
        accuracy = (correct_predictions_counter[label] / true_labels_counter[label]) if label in correct_predictions_counter else 0
        accuracies[label] = accuracy
    
    return accuracies

# Load model components
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"
image_processor = AutoImageProcessor.from_pretrained(repo_id)
tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
model = AutoModel.from_pretrained(repo_id)
clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                         device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(repo_id))

# DataFrame to store all accuracies
all_accuracies = []

# Loop over each fold and test
for fold in range(2):
    # Load the JSON data for the current fold
    with open(f'val_fold_{fold}.json', 'r') as f:
        data = [json.loads(line) for line in f]

    # Extract image paths and labels for the current fold
    image_paths = [item['image'] for item in data]
    labels = [item['caption'] for item in data]

    BATCH_SIZE = 128  # Adjust based on your available memory
    all_predictions = []
    all_true_labels = []

    for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
        batch_images = []
        valid_labels = []
        for path, label in zip(batch_paths, batch_labels):
            try:
                batch_images.append(Image.open(path))
                valid_labels.append(label)
            except (FileNotFoundError, UnidentifiedImageError):
                continue  # Skip images that cannot be opened

        # Get predictions for the batch of images
        predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
        predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

        all_predictions.extend(predicted_labels)
        all_true_labels.extend(valid_labels)

    correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
    accuracy = correct_predictions / len(all_true_labels)
    print(f"Accuracy for model on fold {fold}: {accuracy * 100:.2f}%\n")

    # Calculate the accuracy for each category for the current fold
    category_accuracies = calculate_category_accuracy(all_true_labels, all_predictions)

    # Store the accuracies in a list of dictionaries
    for category, acc in category_accuracies.items():
        all_accuracies.append({'Fold': fold, 'Category': category, 'Accuracy': acc})
    # Add overall accuracy for the current fold to the list
    all_accuracies.append({'Fold': fold, 'Category': 'Overall', 'Accuracy': accuracy})

# Convert the list of dictionaries to a DataFrame
all_accuracies_df = pd.DataFrame(all_accuracies)

# Save the DataFrame to a CSV file
all_accuracies_df.to_csv('./result/org_results.csv', index=False)

# Print out the final DataFrame
print(all_accuracies_df)


/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/transformers/pipelines/base.py:1123: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


Accuracy for model on fold 0: 83.15%

Accuracy for model on fold 1: 84.30%

    Fold                             Category  Accuracy
0      0        a photo of contemporary foyer  0.804124
1      0          a photo of standard kitchen  1.000000
2      0     a photo of contemporary bathroom  0.667910
3      0            a photo of standard foyer  0.868794
4      0         a photo of standard bathroom  0.994197
5      0  a photo of contemporary dining room  0.952632
6      0      a photo of standard living room  0.986486
7      0  a photo of contemporary living room  0.534050
8      0      a photo of contemporary kitchen  0.689655
9      0      a photo of standard dining room  1.000000
10     0                              Overall  0.831540
11     1         a photo of standard bathroom  0.988539
12     1  a photo of contemporary dining room  0.957871
13     1  a photo of contemporary living room  0.597701
14     1            a photo of standard foyer  0.845896
15     1      a photo of con

In [5]:
import numpy as np
import transformers
from datasets import load_dataset
import pathlib
from typing import Generator
from collections import defaultdict
import sys
import json
import os

# Assuming prepare_data_from_dataframe is defined elsewhere in your project

# Fine-tune base model setup
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"
transformers.utils.logging.set_verbosity_error()

# Main training loop
for fold in range(5):  # Five folds
    for i, threshold in enumerate(np.arange(0.90, 1.00, 0.01), start=1):
        # Filename setup for training data at current threshold and fold
        train_json = f'train_fold_{fold}_thr_{int(threshold*100)}.json'
        test_json = f'val_fold_{fold}.json'  # Validation data for current fold

        # Output directory for the trained model
        output_folder = f"./workspace/output/laion-finetuned_v5e7_epoch10_fold{fold}_threshold{i}"
        print(f"Finetuning {repo_id} for fold {fold}, threshold > {threshold:.2f}, saving output to {output_folder}.")

        # Load dataset
        data_files = {'train': train_json, 'validation': test_json}
        dataset = load_dataset("json", data_files=data_files)
        print(f"First image: {dataset['validation'][0]['image']}, caption: '{dataset['validation'][0]['caption']}'")

        !python huggingface_finetune_clip.py \
            --output_dir {output_folder} --model_name_or_path {repo_id} \
            --train_file {train_json} \
            --validation_file {test_json} \
            --image_column image \
            --overwrite_output_dir=True \
            --max_seq_length=77 \
            --num_train_epochs=10 \
            --save_total_limit=5 \
            --caption_column caption \
            --remove_unused_columns=False \
            --do_train \
            --logging_strategy="epoch"\
            --per_device_train_batch_size=128 \
            --dataloader_drop_last=True\
            --learning_rate="1e-6" --warmup_steps="0" --weight_decay 0.1 
        print(f"--\nDONE. If it worked, trained data should be in {output_folder}\n")

Finetuning laion/CLIP-ViT-B-32-laion2B-s34B-b79K for fold 0, threshold > 0.90, saving output to ./workspace/output/laion-finetuned_v5e7_epoch10_fold0_threshold1.


Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

First image: ../data/a photo of standard living room/IMG-C5471443_15.jpg, caption: 'a photo of standard living room'
04/16/2024 15:32:43 - WARNING - __main__ - Process rank: 0, device: cuda:0, n_gpu: 3distributed training: True, 16-bits training: False
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/datasets/load.py:2072: FutureWarning: 'use_auth_token' was deprecated in favor of 'token' in version 2.14.0 and will be removed in 3.0.0.
You can remove this warning by passing 'token=None' instead.
  warnings.warn(
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
Parameter 'function'=<function main.<locals>.filter_corrupt_images at 0x7fe5b8694dc0> of the transform datasets.arrow_dataset.Dataset.filter@2.0.1 couldn't be hashed prope

...

First image: ../data/a photo of standard bathroom/IMG-C5471456_22.jpg, caption: 'a photo of standard bathroom'
04/18/2024 06:59:24 - WARNING - __main__ - Process rank: 0, device: cuda:0, n_gpu: 3distributed training: True, 16-bits training: False
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/datasets/load.py:2072: FutureWarning: 'use_auth_token' was deprecated in favor of 'token' in version 2.14.0 and will be removed in 3.0.0.
You can remove this warning by passing 'token=None' instead.
  warnings.warn(
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
Parameter 'function'=<function main.<locals>.filter_corrupt_images at 0x7f1ebcbacdc0> of the transform datasets.arrow_dataset.Dataset.filter@2.0.1 couldn't be hashed properly, a

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

First image: ../data/a photo of standard bathroom/IMG-C5471456_22.jpg, caption: 'a photo of standard bathroom'
04/18/2024 07:17:25 - WARNING - __main__ - Process rank: 0, device: cuda:0, n_gpu: 3distributed training: True, 16-bits training: False
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/datasets/load.py:2072: FutureWarning: 'use_auth_token' was deprecated in favor of 'token' in version 2.14.0 and will be removed in 3.0.0.
You can remove this warning by passing 'token=None' instead.
  warnings.warn(
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
Parameter 'function'=<function main.<locals>.filter_corrupt_images at 0x7fc7c1f04dc0> of the transform datasets.arrow_dataset.Dataset.filter@2.0.1 couldn't be hashed properly, a

In [13]:
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt
from collections import Counter
import numpy as np
import pandas as pd

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

def calculate_category_accuracy(true_labels, predicted_labels):
    """Calculate the accuracy for each category and return it as a dictionary."""
    accuracies = {}
    true_labels_counter = Counter(true_labels)
    correct_predictions_counter = Counter([true for true, pred in zip(true_labels, predicted_labels) if true == pred])
    
    for label in true_labels_counter:
        accuracy = (correct_predictions_counter[label] / true_labels_counter[label]) if label in correct_predictions_counter else 0
        accuracies[label] = accuracy
    
    return accuracies
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"
BATCH_SIZE = 128  # Adjust based on your available memory
results = []  # List to hold accuracy results

# Loop for each fold and each threshold
for fold in range(2):
    for idx, threshold in enumerate(np.arange(0.91, 1.00, 0.01)):
        model_dir = f"./workspace/output/backup_ckpts/laion-finetuned_v5e7_epoch10_fold{fold}_threshold{idx+1}"
        test_json = f'val_fold_{fold}.json'  # Test JSON file for the current fold
        print(f"Evaluating with model from {model_dir}...")

        # Load the JSON data for testing
        with open(test_json, 'r') as f:
            data = [json.loads(line) for line in f]

        # Extract image paths and labels
        image_paths = [item['image'] for item in data]
        labels = [item['caption'] for item in data]

        # Initialize model components
        image_processor = AutoImageProcessor.from_pretrained(repo_id)
        tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
        model = AutoModel.from_pretrained(model_dir)
        clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                                 device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(model_dir))

        all_predictions = []
        all_true_labels = []

        # Process images in batches
        for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
            batch_images = []
            valid_labels = []
            for path, label in zip(batch_paths, batch_labels):
                try:
                    batch_images.append(Image.open(path))
                    valid_labels.append(label)
                except (FileNotFoundError, UnidentifiedImageError):
                    continue  # Skip images that cannot be opened

            # Get predictions for the batch of images
            predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
            predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

            all_predictions.extend(predicted_labels)
            all_true_labels.extend(valid_labels)


        # Calculate accuracy
        correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
        accuracy = correct_predictions / len(all_true_labels)
        print(f"Accuracy for model on fold {fold} with threshold {threshold:.2f}: {accuracy * 100:.2f}%\n")

        # Calculate the accuracy for each category
        category_accuracies = calculate_category_accuracy(all_true_labels, all_predictions)
        for category, acc in category_accuracies.items():
            results.append({
                'Fold': fold,
                'Threshold': f">{threshold:.2f}",
                'Category': category,
                'Accuracy': acc
            })
        print("--\nDONE\n")

# Create DataFrame from results and save to CSV
results_df = pd.DataFrame(results)
results_df.to_csv('./result/ours_results.csv', index=False)
print("All results saved to model_evaluation_results.csv")



Evaluating with model from ./workspace/output/backup_ckpts/laion-finetuned_v5e7_epoch10_fold0_threshold1...


/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/transformers/pipelines/base.py:1123: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


Accuracy for model on fold 0 with threshold 0.91: 96.96%

--
DONE

Evaluating with model from ./workspace/output/backup_ckpts/laion-finetuned_v5e7_epoch10_fold0_threshold2...
Accuracy for model on fold 0 with threshold 0.92: 97.10%

--
DONE

Evaluating with model from ./workspace/output/backup_ckpts/laion-finetuned_v5e7_epoch10_fold0_threshold3...
Accuracy for model on fold 0 with threshold 0.93: 96.72%

--
DONE

Evaluating with model from ./workspace/output/backup_ckpts/laion-finetuned_v5e7_epoch10_fold0_threshold4...
Accuracy for model on fold 0 with threshold 0.94: 96.40%

--
DONE

Evaluating with model from ./workspace/output/backup_ckpts/laion-finetuned_v5e7_epoch10_fold0_threshold5...
Accuracy for model on fold 0 with threshold 0.95: 96.40%

--
DONE

Evaluating with model from ./workspace/output/backup_ckpts/laion-finetuned_v5e7_epoch10_fold0_threshold6...
Accuracy for model on fold 0 with threshold 0.96: 95.84%

--
DONE

Evaluating with model from ./workspace/output/backup_ckpts

In [9]:
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt
from collections import Counter
import numpy as np
import pandas as pd

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

def calculate_category_accuracy(true_labels, predicted_labels):
    """Calculate the accuracy for each category and return it as a dictionary."""
    accuracies = {}
    true_labels_counter = Counter(true_labels)
    correct_predictions_counter = Counter([true for true, pred in zip(true_labels, predicted_labels) if true == pred])
    
    for label in true_labels_counter:
        accuracy = (correct_predictions_counter[label] / true_labels_counter[label]) if label in correct_predictions_counter else 0
        accuracies[label] = accuracy
    
    return accuracies

BATCH_SIZE = 128  # Adjust based on your available memory
results = []

# Loop for each fold and each threshold
for fold in range(5):
    for threshold in np.arange(0.90, 1.00, 0.01):
        model_dir = f"./workspace/output/laion-finetuned_v5e7_epoch10_fold{fold}_threshold{int(threshold*100)}"
        test_json = f'val_fold_{fold}.json'  # Test JSON file for the current fold
        print(f"Evaluating with model from {model_dir}...")

        # Load the JSON data for testing
        with open(test_json, 'r') as f:
            data = [json.loads(line) for line in f]

        # Extract image paths and labels
        image_paths = [item['image'] for item in data]
        labels = [item['caption'] for item in data]

        # Initialize model components
        image_processor = AutoImageProcessor.from_pretrained(model_dir)
        tokenizer = AutoTokenizer.from_pretrained(model_dir, config=AutoConfig.from_pretrained(model_dir))
        model = AutoModel.from_pretrained(model_dir)
        clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                                 device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(model_dir))

        all_predictions = []
        all_true_labels = []

        # Process images in batches
        for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
            batch_images = []
            valid_labels = []
            for path, label in zip(batch_paths, batch_labels):
                try:
                    batch_images.append(Image.open(path))
                    valid_labels.append(label)
                except (FileNotFoundError, UnidentifiedImageError):
                    continue  # Skip images that cannot be opened

            # Get predictions for the batch of images
            predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
            predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

            all_predictions.extend(predicted_labels)
            all_true_labels.extend(valid_labels)

        # Calculate accuracy
        correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
        accuracy = correct_predictions / len(all_true_labels)
        print(f"Accuracy for model on fold {fold} with threshold {threshold:.2f}: {accuracy * 100:.2f}%\n")

        # Calculate the accuracy for each category
        category_accuracies = calculate_category_accuracy(all_true_labels, all_predictions)
        for category, acc in category_accuracies.items():
            results.append({
                'Fold': fold,
                'Threshold': f">{threshold:.2f}",
                'Category': category,
                'Accuracy': acc
            })
        print("--\nDONE\n")

# Create DataFrame from results and save to CSV
results_df = pd.DataFrame(results)
results_df.to_csv('./result/ours_results.csv', index=False)
print("All results saved to model_evaluation_results.csv")

# change to org test and add all predict details into df, future may generate con-mat

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain1...
Accuracy for model 1: 97.08%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain2...
Accuracy for model 2: 97.17%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain3...
Accuracy for model 3: 98.20%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain4...
Accuracy for model 4: 96.79%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain5...
Accuracy for model 5: 96.75%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain6...
Accuracy for model 6: 96.33%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain7...
Accuracy for model 7: 95.81%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain8...
Accuracy for model 8: 94.56%



# read data directly from csv 0.95 as test

In [22]:
import pandas as pd
import json

def prepare_data_from_dataframe(df: pd.DataFrame, output_file: str) -> str:
    """Prepare data for finetuning by reading from a DataFrame."""
    data = []

    # Process data
    for _, row in df.iterrows():
        image_path = f"../data/{row['max_key']}/{row['path'].split('/')[-1]}"
        data.append({"image": image_path, "caption": row['max_key']})

    # Save the data in JSON format
    with open(output_file, "w") as f:
        for item in data:
            json.dump(item, f)
            f.write("\n")

    return output_file


# Load the CSV file
df = pd.read_csv('labels.csv')
df = df[df['max_key'] != 'error']
df = df[df['max_key'] != 'a photo of other indoor space: not kitchen, not bathroom, not living room, not dining room, not foyer']
df = df[df['max_key'] != 'it is a artificial photo']
df = df[df['max_key'] != 'a photo of outdoor space']

# Filter samples with max_value > 0.9
test_df = df[df['max_value'] == 0.95]
threshold_df = df[(df['max_value'] > 0.9) & (~df.index.isin(test_df.index))]


test_json = prepare_data_from_dataframe(test_df, 'val.json')


In [23]:
import numpy as np
# Finetune base model
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"
batch_size = 64
num_train_epochs = 100

transformers.utils.logging.set_verbosity_error()

# Loop for different thresholds
for i, threshold in enumerate(np.arange(0.91, 1.0, 0.01), start=1):
    if threshold is 0.95:
        continue
    threshold_df = df[df['max_value'] > threshold]
    threshold_df = threshold_df[threshold_df['max_value'] != 0.95]
    train_json = f'train{i}.json'
    prepare_data_from_dataframe(threshold_df, train_json)

    output_folder = f"./workspace/output/laion-finetuned_v5e7_epoch10_vtrain{i}"
    print(f"Finetuning {repo_id} for threshold > {threshold:.2f}, saving output to {output_folder}.")
    data_files = {'train': train_json, 'validation': test_json}
    dataset = load_dataset("json", data_files=data_files)
    print(f"first image: {dataset['validation'][0]['image']}, caption: '{dataset['validation'][0]['caption']}'")

    !python huggingface_finetune_clip.py \
        --output_dir {output_folder} --model_name_or_path {repo_id} \
        --train_file {train_json} \
        --validation_file {test_json} \
        --image_column image \
        --overwrite_output_dir=True \
        --max_seq_length=77 \
        --num_train_epochs=10 \
        --save_total_limit=5 \
        --caption_column caption \
        --remove_unused_columns=False \
        --do_train \
        --logging_strategy="epoch"\
        --per_device_train_batch_size=128 \
        --dataloader_drop_last=True\
        --learning_rate="1e-6" --warmup_steps="0" --weight_decay 0.1 
    print(f"--\nDONE. If it worked, trained data should be in {output_folder}\n")

<>:11: SyntaxWarning: "is" with a literal. Did you mean "=="?
<>:11: SyntaxWarning: "is" with a literal. Did you mean "=="?
/tmp/ipykernel_3654472/3070016425.py:11: SyntaxWarning: "is" with a literal. Did you mean "=="?
  if threshold is 0.95:


Finetuning laion/CLIP-ViT-B-32-laion2B-s34B-b79K for threshold > 0.91, saving output to ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain1.


Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

...

first image: ../data/a photo of contemporary foyer/IMG-C5471460_10.jpg, caption: 'a photo of contemporary foyer'
03/22/2024 19:06:42 - WARNING - __main__ - Process rank: 0, device: cuda:0, n_gpu: 3distributed training: True, 16-bits training: False
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/datasets/load.py:2072: FutureWarning: 'use_auth_token' was deprecated in favor of 'token' in version 2.14.0 and will be removed in 3.0.0.
You can remove this warning by passing 'token=None' instead.
  warnings.warn(
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
Parameter 'function'=<function main.<locals>.filter_corrupt_images at 0x7f3a009b0d30> of the transform datasets.arrow_dataset.Dataset.filter@2.0.1 couldn't be hashed properly,

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

first image: ../data/a photo of contemporary foyer/IMG-C5471460_10.jpg, caption: 'a photo of contemporary foyer'
03/22/2024 19:30:25 - WARNING - __main__ - Process rank: 0, device: cuda:0, n_gpu: 3distributed training: True, 16-bits training: False
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/datasets/load.py:2072: FutureWarning: 'use_auth_token' was deprecated in favor of 'token' in version 2.14.0 and will be removed in 3.0.0.
You can remove this warning by passing 'token=None' instead.
  warnings.warn(
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
Parameter 'function'=<function main.<locals>.filter_corrupt_images at 0x7f0abc714d30> of the transform datasets.arrow_dataset.Dataset.filter@2.0.1 couldn't be hashed properly,

In [24]:
# 95
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Load the JSON data
with open('val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 128  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"

# Loop for different finetuned models
for i in range(1, 10):  # Assuming you have 9 finetuned models
    dir = f"./workspace/output/laion-finetuned_v5e7_epoch10_vtrain{i}"
    print(f"Evaluating with model from {dir}...")

    image_processor = AutoImageProcessor.from_pretrained(repo_id)
    tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
    model = AutoModel.from_pretrained(dir)
    clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                             device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(dir))

    all_predictions = []
    all_true_labels = []

    for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
        batch_images = []
        valid_labels = []
        for path, label in zip(batch_paths, batch_labels):
            try:
                batch_images.append(Image.open(path))
                valid_labels.append(label)
            except (FileNotFoundError, UnidentifiedImageError):
                continue  # Skip images that cannot be opened

        # Get predictions for the batch of images
        predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
        predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

        all_predictions.extend(predicted_labels)
        all_true_labels.extend(valid_labels)

    correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
    accuracy = correct_predictions / len(all_true_labels)
    print(f"Accuracy for model {i}: {accuracy * 100:.2f}%\n")


Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain1...


/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/transformers/pipelines/base.py:1123: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


Accuracy for model 1: 96.96%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain2...
Accuracy for model 2: 97.10%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain3...
Accuracy for model 3: 96.72%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain4...
Accuracy for model 4: 96.40%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain5...
Accuracy for model 5: 96.40%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain6...
Accuracy for model 6: 95.84%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain7...
Accuracy for model 7: 95.79%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain8...
Accuracy for model 8: 94.62%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain9...
Accuracy for model 9: 93.12%



In [25]:
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Load the JSON data
with open('val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 128  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"


image_processor = AutoImageProcessor.from_pretrained(repo_id)
tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
model = AutoModel.from_pretrained(repo_id)
clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                         device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(repo_id))

all_predictions = []
all_true_labels = []

for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
    batch_images = []
    valid_labels = []
    for path, label in zip(batch_paths, batch_labels):
        try:
            batch_images.append(Image.open(path))
            valid_labels.append(label)
        except (FileNotFoundError, UnidentifiedImageError):
            continue  # Skip images that cannot be opened

    # Get predictions for the batch of images
    predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
    predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

    all_predictions.extend(predicted_labels)
    all_true_labels.extend(valid_labels)

correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
accuracy = correct_predictions / len(all_true_labels)
print(f"Accuracy for model org: {accuracy * 100:.2f}%\n")

Accuracy for model 9: 83.15%



# test on five room task

In [44]:
import os
import json
import os
import pathlib
from typing import Generator
from collections import defaultdict
import datasets
from datasets import load_dataset
import sys

def collect_images_from_directory(directory: str) -> dict:
    """Collect images from a specified directory and group them by label."""
    images_per_label = defaultdict(list)
    
    subfolders = [d for d in os.listdir(directory) if os.path.isdir(os.path.join(directory, d))]
    for subfolder in subfolders:
        label = subfolder
        subfolder_path = os.path.join(directory, subfolder)
        for filename in os.listdir(subfolder_path):
            if filename.endswith('.jpg') or filename.endswith('.png'):
                images_per_label[label].append(os.path.join(subfolder_path, filename))
                
    return images_per_label

def prepare_data_for_finetuning(train_dir: str, test_dir: str) -> tuple:
    """Prepare data for finetuning by reading images from specified train and test directories."""
    train_data = []
    val_data = []

    # Collect training images
    train_images_per_label = collect_images_from_directory(train_dir)
    for label, images in train_images_per_label.items():
        train_data.extend([{"image": img, "caption": label} for img in images])

    # Collect testing images
    test_images_per_label = collect_images_from_directory(test_dir)
    for label, images in test_images_per_label.items():
        val_data.extend([{"image": img, "caption": label} for img in images])

    # Save the data in JSON format in the code directory
    train_file = "room_train.json"
    val_file = "room_val.json"
    with open(train_file, "w") as f:
        for item in train_data:
            json.dump(item, f)
            f.write("\n")
    with open(val_file, "w") as f:
        for item in val_data:
            json.dump(item, f)
            f.write("\n")
    
    return train_file, val_file

# Usage:
train_json, test_json = prepare_data_for_finetuning("../room_5", "../room_5")
data_files = {'train': train_json, 'validation': test_json}

# test loading it back in

dataset = load_dataset("json", data_files=data_files)
print(f"first image: {dataset['validation'][0]['image']}, caption: '{dataset['validation'][0]['caption']}'")

print(sys.executable)
!which pip3
dataset['validation']

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

first image: ../room_5/a photo of kitchen/gsun_1c5c2085ba8b7d4a176739aab0998c8d.jpg, caption: 'a photo of kitchen'
/home/haojin/anaconda3/envs/huggingface/bin/python
/home/haojin/anaconda3/envs/huggingface/bin/pip3


Dataset({
    features: ['image', 'caption'],
    num_rows: 102625
})

In [45]:
# test on original ckpt
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Load the JSON data
with open('room_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 128  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"


image_processor = AutoImageProcessor.from_pretrained(repo_id)
tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
model = AutoModel.from_pretrained(repo_id)
clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                         device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(repo_id))

all_predictions = []
all_true_labels = []

for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
    batch_images = []
    valid_labels = []
    for path, label in zip(batch_paths, batch_labels):
        try:
            batch_images.append(Image.open(path))
            valid_labels.append(label)
        except (FileNotFoundError, UnidentifiedImageError):
            continue  # Skip images that cannot be opened

    # Get predictions for the batch of images
    predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
    predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

    all_predictions.extend(predicted_labels)
    all_true_labels.extend(valid_labels)

correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
accuracy = correct_predictions / len(all_true_labels)
print(f"Accuracy for model: {accuracy * 100:.2f}%\n")

Accuracy for model: 99.97%



In [46]:
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Load the JSON data
with open('room_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 128  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"

# Loop for different finetuned models
for i in range(1, 10):  # Assuming you have 9 finetuned models
    dir = f"./workspace/output/laion-finetuned_v5e7_epoch10_vtrain{i}"
    print(f"Evaluating with model from {dir}...")

    image_processor = AutoImageProcessor.from_pretrained(repo_id)
    tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
    model = AutoModel.from_pretrained(dir)
    clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                             device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(dir))

    all_predictions = []
    all_true_labels = []

    for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
        batch_images = []
        valid_labels = []
        for path, label in zip(batch_paths, batch_labels):
            try:
                batch_images.append(Image.open(path))
                valid_labels.append(label)
            except (FileNotFoundError, UnidentifiedImageError):
                continue  # Skip images that cannot be opened

        # Get predictions for the batch of images
        predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
        predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

        all_predictions.extend(predicted_labels)
        all_true_labels.extend(valid_labels)

    correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
    accuracy = correct_predictions / len(all_true_labels)
    print(f"Accuracy for model {i}: {accuracy * 100:.2f}%\n")


Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain1...
Accuracy for model 1: 99.96%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain2...
Accuracy for model 2: 99.96%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain3...
Accuracy for model 3: 99.96%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain4...
Accuracy for model 4: 99.96%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain5...
Accuracy for model 5: 99.96%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain6...
Accuracy for model 6: 99.96%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain7...
Accuracy for model 7: 99.97%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain8...
Accuracy for model 8: 99.97%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch

# test on orginal dataset

In [2]:
import os
import json
import os
import pathlib
from typing import Generator
from collections import defaultdict
import datasets
from datasets import load_dataset
import sys

def collect_images_from_directory(directory: str) -> dict:
    """Collect images from a specified directory and group them by label."""
    images_per_label = defaultdict(list)
    
    subfolders = [d for d in os.listdir(directory) if os.path.isdir(os.path.join(directory, d))]
    for subfolder in subfolders:
        label = subfolder
        subfolder_path = os.path.join(directory, subfolder)
        for filename in os.listdir(subfolder_path):
            if filename.endswith('.jpg') or filename.endswith('.png'):
                images_per_label[label].append(os.path.join(subfolder_path, filename))
                
    return images_per_label

def prepare_data_for_finetuning(train_dir: str, test_dir: str) -> tuple:
    """Prepare data for finetuning by reading images from specified train and test directories."""
    train_data = []
    val_data = []

    # Collect training images
    train_images_per_label = collect_images_from_directory(train_dir)
    for label, images in train_images_per_label.items():
        train_data.extend([{"image": img, "caption": label} for img in images])

    # Collect testing images
    test_images_per_label = collect_images_from_directory(test_dir)
    for label, images in test_images_per_label.items():
        val_data.extend([{"image": img, "caption": label} for img in images])

    # Save the data in JSON format in the code directory
    train_file = "kb_train.json"
    val_file = "kb_val.json"
    with open(train_file, "w") as f:
        for item in train_data:
            json.dump(item, f)
            f.write("\n")
    with open(val_file, "w") as f:
        for item in val_data:
            json.dump(item, f)
            f.write("\n")
    
    return train_file, val_file

# Usage:
train_json, test_json = prepare_data_for_finetuning("../class_4", "../class_4")
data_files = {'train': train_json, 'validation': test_json}

# test loading it back in

dataset = load_dataset("json", data_files=data_files)
print(f"first image: {dataset['validation'][0]['image']}, caption: '{dataset['validation'][0]['caption']}'")

print(sys.executable)
!which pip3
dataset['validation']

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

first image: ../class_4/a photo of standard bathroom/IMG-C5472473_15.jpg, caption: 'a photo of standard bathroom'
/home/haojin/anaconda3/envs/huggingface/bin/python
/home/haojin/anaconda3/envs/huggingface/bin/pip3


Dataset({
    features: ['image', 'caption'],
    num_rows: 752
})

In [3]:
# test on original ckpt
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Load the JSON data
with open('kb_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 128  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"


image_processor = AutoImageProcessor.from_pretrained(repo_id)
tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
model = AutoModel.from_pretrained(repo_id)
clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                         device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(repo_id))

all_predictions = []
all_true_labels = []

for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
    batch_images = []
    valid_labels = []
    for path, label in zip(batch_paths, batch_labels):
        try:
            batch_images.append(Image.open(path))
            valid_labels.append(label)
        except (FileNotFoundError, UnidentifiedImageError):
            continue  # Skip images that cannot be opened

    # Get predictions for the batch of images
    predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
    predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

    all_predictions.extend(predicted_labels)
    all_true_labels.extend(valid_labels)

correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
accuracy = correct_predictions / len(all_true_labels)
print(f"Accuracy for model: {accuracy * 100:.2f}%\n")

Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model: 99.87%



In [4]:
# accuracy per class
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Load the JSON data
with open('kb_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 128  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"

image_processor = AutoImageProcessor.from_pretrained(repo_id)
tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
model = AutoModel.from_pretrained(repo_id)
clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                         device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(repo_id))

all_predictions = []
all_true_labels = []

class_accuracy = {}  # Dictionary to track accuracy per class

for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
    batch_images = []
    valid_labels = []
    for path, label in zip(batch_paths, batch_labels):
        try:
            batch_images.append(Image.open(path))
            valid_labels.append(label)
        except (FileNotFoundError, UnidentifiedImageError):
            continue  # Skip images that cannot be opened

    # Get predictions for the batch of images
    predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
    predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

    all_predictions.extend(predicted_labels)
    all_true_labels.extend(valid_labels)

    # Update class accuracy counts
    for true_label, predicted_label in zip(valid_labels, predicted_labels):
        if true_label not in class_accuracy:
            class_accuracy[true_label] = {'correct': 0, 'total': 0}
        class_accuracy[true_label]['total'] += 1
        if true_label == predicted_label:
            class_accuracy[true_label]['correct'] += 1

# Print accuracy per class and calculate mean accuracy
mean_accuracy = 0
for class_label, counts in class_accuracy.items():
    class_acc = counts['correct'] / counts['total']
    mean_accuracy += class_acc
    print(f"Accuracy for class '{class_label}': {class_acc * 100:.2f}%")
mean_accuracy /= len(class_accuracy)
print(f"\nMean accuracy over all classes: {mean_accuracy * 100:.2f}%\n")


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for class 'a photo of standard bathroom': 100.00%
Accuracy for class 'a photo of standard kitchen': 100.00%
Accuracy for class 'a photo of contemporary bathroom': 99.15%
Accuracy for class 'a photo of contemporary kitchen': 100.00%

Mean accuracy over all classes: 99.79%



In [5]:
# accuracy per class
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Load the JSON data
with open('kb_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 128  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"
dir = "./workspace/output/laion-finetuned_v5e7_epoch10_vtrain2"
image_processor = AutoImageProcessor.from_pretrained(repo_id)
tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
model = AutoModel.from_pretrained(dir)
clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                         device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(dir))

all_predictions = []
all_true_labels = []

class_accuracy = {}  # Dictionary to track accuracy per class

for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
    batch_images = []
    valid_labels = []
    for path, label in zip(batch_paths, batch_labels):
        try:
            batch_images.append(Image.open(path))
            valid_labels.append(label)
        except (FileNotFoundError, UnidentifiedImageError):
            continue  # Skip images that cannot be opened

    # Get predictions for the batch of images
    predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
    predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

    all_predictions.extend(predicted_labels)
    all_true_labels.extend(valid_labels)

    # Update class accuracy counts
    for true_label, predicted_label in zip(valid_labels, predicted_labels):
        if true_label not in class_accuracy:
            class_accuracy[true_label] = {'correct': 0, 'total': 0}
        class_accuracy[true_label]['total'] += 1
        if true_label == predicted_label:
            class_accuracy[true_label]['correct'] += 1

# Print accuracy per class and calculate mean accuracy
mean_accuracy = 0
for class_label, counts in class_accuracy.items():
    class_acc = counts['correct'] / counts['total']
    mean_accuracy += class_acc
    print(f"Accuracy for class '{class_label}': {class_acc * 100:.2f}%")
mean_accuracy /= len(class_accuracy)
print(f"\nMean accuracy over all classes: {mean_accuracy * 100:.2f}%\n")


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for class 'a photo of standard bathroom': 100.00%
Accuracy for class 'a photo of standard kitchen': 100.00%
Accuracy for class 'a photo of contemporary bathroom': 99.15%
Accuracy for class 'a photo of contemporary kitchen': 100.00%

Mean accuracy over all classes: 99.79%



In [6]:
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import matplotlib.pyplot as plt

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Load the JSON data
with open('kb_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 128  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"

# Loop for different finetuned models
for i in range(1, 10):  # Assuming you have 9 finetuned models
    dir = f"./workspace/output/laion-finetuned_v5e7_epoch10_vtrain{i}"
    print(f"Evaluating with model from {dir}...")

    image_processor = AutoImageProcessor.from_pretrained(repo_id)
    tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
    model = AutoModel.from_pretrained(dir)
    clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                             device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(dir))

    all_predictions = []
    all_true_labels = []

    for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
        batch_images = []
        valid_labels = []
        for path, label in zip(batch_paths, batch_labels):
            try:
                batch_images.append(Image.open(path))
                valid_labels.append(label)
            except (FileNotFoundError, UnidentifiedImageError):
                continue  # Skip images that cannot be opened

        # Get predictions for the batch of images
        predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
        predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

        all_predictions.extend(predicted_labels)
        all_true_labels.extend(valid_labels)

    correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
    accuracy = correct_predictions / len(all_true_labels)
    print(f"Accuracy for model {i}: {accuracy * 100:.2f}%\n")


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain1...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 1: 99.73%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain2...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


...

Accuracy for model 6: 99.87%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain7...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 7: 99.87%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain8...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 8: 99.87%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_vtrain9...
Accuracy for model 9: 99.87%



# quantization small model

In [ ]:
import os
import torch

# Make only the first GPU visible (GPU 0)
os.environ["CUDA_VISIBLE_DEVICES"] = ""

# Check if CUDA (GPU support) is available
if torch.cuda.is_available():
    print(f"CUDA is available. Number of GPUs: {torch.cuda.device_count()}")
    
    # Loop through and print details of each GPU
    for i in range(torch.cuda.device_count()):
        print(f"GPU {i}: {torch.cuda.get_device_name(i)}")
else:
    print("CUDA is not available. Only CPU will be used.")


In [2]:
from accelerate.utils import BnbQuantizationConfig
bnb_quantization_config = BnbQuantizationConfig(load_in_8bit=True)
from accelerate.utils import load_and_quantize_model
from transformers import CLIPProcessor, CLIPModel, AutoModel
from accelerate import init_empty_weights
from transformers import AutoTokenizer, AutoConfig, AutoModel,AutoModelForZeroShotImageClassification
config = AutoConfig.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
with init_empty_weights():
    empty_model = AutoModelForZeroShotImageClassification.from_config(config)
    #CLIP(config=AutoConfig.from_pretrained("openai/clip-vit-large-patch14"))

# Move the model to GPU 0
print(empty_model.device)
dir = "./workspace/output/laion-finetuned_v5e7_epoch10_vtrain2"
model = AutoModel.from_pretrained(dir)
from huggingface_hub import snapshot_download
weights_location = "./workspace/output/laion-finetuned_v5e7_epoch10_vtrain2/model.safetensors"
quantized_model = load_and_quantize_model(empty_model, weights_location=weights_location, bnb_quantization_config=bnb_quantization_config, device_map = "auto")

meta


In [3]:
import os
import csv
from transformers import CLIPProcessor, CLIPModel, pipeline, CLIPImageProcessor
from PIL import Image
from transformers import AutoTokenizer, AutoConfig, AutoModel,AutoImageProcessor
import matplotlib.pyplot as plt
import time
import json

# Load the JSON data
with open('kb_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

repo_id =  "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"
dir = "./workspace/output/laion-finetuned_v5e7_epoch10_vtrain2"
image_processor = AutoImageProcessor.from_pretrained(
    repo_id
)
tokenizer = AutoTokenizer.from_pretrained(repo_id, 
                                          config=AutoConfig.from_pretrained(repo_id))
model = quantized_model
clip_pipeline = pipeline(model=model,task="zero-shot-image-classification", tokenizer=tokenizer,
                    image_processor=image_processor, config=AutoConfig.from_pretrained(dir),
                        device_map="auto", model_kwargs={"load_in_8bit": True})

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

BATCH_SIZE = 256  # Adjust based on your available memory

all_predictions = []
all_true_labels = []
time_eval = []

for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
    batch_images = []
    valid_labels = []
    for path, label in zip(batch_paths, batch_labels):
        try:
            batch_images.append(Image.open(path))
            valid_labels.append(label)
        except (FileNotFoundError, UnidentifiedImageError):
            continue  # Skip images that cannot be opened

    # Get predictions for the batch of images
    predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
    predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

    all_predictions.extend(predicted_labels)
    all_true_labels.extend(valid_labels)

correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
accuracy = correct_predictions / len(all_true_labels)
print(f"Accuracy for model {i}: {accuracy * 100:.2f}%\n")


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 0: 96.81%



## random testing result

### original model

In [4]:
from accelerate.utils import BnbQuantizationConfig
bnb_quantization_config = BnbQuantizationConfig(load_in_8bit=True)
from accelerate.utils import load_and_quantize_model
from transformers import CLIPProcessor, CLIPModel, AutoModel
from accelerate import init_empty_weights
from transformers import AutoTokenizer, AutoConfig, AutoModel,AutoModelForZeroShotImageClassification
config = AutoConfig.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
with init_empty_weights():
    empty_model = AutoModelForZeroShotImageClassification.from_config(config)
    #CLIP(config=AutoConfig.from_pretrained("openai/clip-vit-large-patch14"))

# Move the model to GPU 0
print(empty_model.device)
model = AutoModel.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
from huggingface_hub import snapshot_download
weights_location = snapshot_download(repo_id="laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
quantized_model = load_and_quantize_model(empty_model, weights_location=weights_location, 
                                          bnb_quantization_config=bnb_quantization_config, device_map = "auto")



meta


Fetching 14 files:   0%|          | 0/14 [00:00<?, ?it/s]

In [5]:
import os
import csv
from transformers import CLIPProcessor, CLIPModel, pipeline, CLIPImageProcessor
from PIL import Image
from transformers import AutoTokenizer, AutoConfig, AutoModel,AutoImageProcessor
import matplotlib.pyplot as plt
import time
import json

# Load the JSON data
with open('val_random.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

repo_id =  "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"

image_processor = AutoImageProcessor.from_pretrained(
    repo_id
)
tokenizer = AutoTokenizer.from_pretrained(repo_id, 
                                          config=AutoConfig.from_pretrained(repo_id))
model = quantized_model
clip_pipeline = pipeline(model=model,task="zero-shot-image-classification", tokenizer=tokenizer,
                    image_processor=image_processor, config=AutoConfig.from_pretrained(repo_id),
                        device_map="auto", model_kwargs={"load_in_8bit": True})

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

BATCH_SIZE = 256  # Adjust based on your available memory

all_predictions = []
all_true_labels = []
time_eval = []

for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
    batch_images = []
    valid_labels = []
    for path, label in zip(batch_paths, batch_labels):
        try:
            batch_images.append(Image.open(path))
            valid_labels.append(label)
        except (FileNotFoundError, UnidentifiedImageError):
            continue  # Skip images that cannot be opened

    # Get predictions for the batch of images
    predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
    predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

    all_predictions.extend(predicted_labels)
    all_true_labels.extend(valid_labels)

correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
accuracy = correct_predictions / len(all_true_labels)
print(f"Accuracy for model {i}: {accuracy * 100:.2f}%\n")


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.
/home/haojin/anaconda3/envs/huggingface/lib/python3.10/site-packages/transformers/pipelines/base.py:1123: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


Accuracy for model 9: 85.71%



### our trained models

In [6]:
from accelerate.utils import BnbQuantizationConfig, load_and_quantize_model
from transformers import CLIPProcessor, CLIPModel, AutoTokenizer, AutoConfig, AutoModelForZeroShotImageClassification, pipeline, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import json

# Load the JSON data for evaluation
with open('val_random.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 256  # Adjust based on your available memory

# Define a function to process images in chunks
def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Base configuration
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"
bnb_quantization_config = BnbQuantizationConfig(load_in_8bit=True)

# Iterate over the 10 models
for i in range(1, 10):  # Assuming you have 19 finetuned models
    dir = f"./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain{i}"
    print(f"Evaluating with model from {dir}...")
    
    # Load and quantize model
    with init_empty_weights():
        empty_model = AutoModelForZeroShotImageClassification.from_config(AutoConfig.from_pretrained(repo_id))

    # Load the model from the directory
    weights_location = f"{dir}/model.safetensors"
    quantized_model = load_and_quantize_model(empty_model, weights_location=weights_location, bnb_quantization_config=bnb_quantization_config, device_map="auto")

    # Initialize tokenizer and processor
    tokenizer = AutoTokenizer.from_pretrained(repo_id)
    image_processor = AutoImageProcessor.from_pretrained(repo_id)
    
    # Initialize the pipeline without the device argument
    clip_pipeline = pipeline(
        model=quantized_model,
        task="zero-shot-image-classification",
        tokenizer=tokenizer,
        image_processor=image_processor,
        config=AutoConfig.from_pretrained(repo_id),
        model_kwargs={"load_in_8bit": True}
    )

    all_predictions = []
    all_true_labels = []

        # Process images in chunks and evaluate
    for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
        batch_images = []
        valid_labels = []
        for path, label in zip(batch_paths, batch_labels):
            try:
                # Open image and append to batch_images
                with Image.open(path) as img:
                    batch_images.append(img.convert("RGB"))
                valid_labels.append(label)
            except (FileNotFoundError, UnidentifiedImageError):
                # Skip images that cannot be opened
                continue

        # Get predictions for the batch of images
        try:
            predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
            predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction
            all_predictions.extend(predicted_labels)
            all_true_labels.extend(valid_labels)
        except Exception as e:
            print(f"An error occurred during prediction: {e}")
            continue

    # Calculate the accuracy for the current model
    correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
    accuracy = correct_predictions / len(all_true_labels) if all_true_labels else 0
    print(f"Accuracy for model {i}: {accuracy * 100:.2f}%\n")



Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain1...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 1: 97.06%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain2...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 2: 97.15%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain3...


...

Accuracy for model 7: 95.59%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain8...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 8: 94.62%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain9...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 9: 92.34%



## kitchen and bathroom result

In [9]:
#original model
from accelerate.utils import BnbQuantizationConfig
bnb_quantization_config = BnbQuantizationConfig(load_in_8bit=True)
from accelerate.utils import load_and_quantize_model
from transformers import CLIPProcessor, CLIPModel, AutoModel
from accelerate import init_empty_weights
from transformers import AutoTokenizer, AutoConfig, AutoModel,AutoModelForZeroShotImageClassification
config = AutoConfig.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
with init_empty_weights():
    empty_model = AutoModelForZeroShotImageClassification.from_config(config)
    #CLIP(config=AutoConfig.from_pretrained("openai/clip-vit-large-patch14"))

# Move the model to GPU 0
print(empty_model.device)
model = AutoModel.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
from huggingface_hub import snapshot_download
weights_location = snapshot_download(repo_id="laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
quantized_model = load_and_quantize_model(empty_model, weights_location=weights_location, 
                                          bnb_quantization_config=bnb_quantization_config, device_map = "auto")

import os
import csv
from transformers import CLIPProcessor, CLIPModel, pipeline, CLIPImageProcessor
from PIL import Image
from transformers import AutoTokenizer, AutoConfig, AutoModel,AutoImageProcessor
import matplotlib.pyplot as plt
import time
import json

# Load the JSON data
with open('kb_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

repo_id =  "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"

image_processor = AutoImageProcessor.from_pretrained(
    repo_id
)
tokenizer = AutoTokenizer.from_pretrained(repo_id, 
                                          config=AutoConfig.from_pretrained(repo_id))
model = quantized_model
clip_pipeline = pipeline(model=model,task="zero-shot-image-classification", tokenizer=tokenizer,
                    image_processor=image_processor, config=AutoConfig.from_pretrained(repo_id),
                        device_map="auto", model_kwargs={"load_in_8bit": True})

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

BATCH_SIZE = 256  # Adjust based on your available memory

all_predictions = []
all_true_labels = []
time_eval = []

for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
    batch_images = []
    valid_labels = []
    for path, label in zip(batch_paths, batch_labels):
        try:
            batch_images.append(Image.open(path))
            valid_labels.append(label)
        except (FileNotFoundError, UnidentifiedImageError):
            continue  # Skip images that cannot be opened

    # Get predictions for the batch of images
    predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
    predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

    all_predictions.extend(predicted_labels)
    all_true_labels.extend(valid_labels)

correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
accuracy = correct_predictions / len(all_true_labels)
print(f"Accuracy for model {i}: {accuracy * 100:.2f}%\n")


meta


Fetching 14 files:   0%|          | 0/14 [00:00<?, ?it/s]

Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 0: 95.08%



In [10]:
from accelerate.utils import BnbQuantizationConfig, load_and_quantize_model
from transformers import CLIPProcessor, CLIPModel, AutoTokenizer, AutoConfig, AutoModelForZeroShotImageClassification, pipeline, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import json

# Load the JSON data for evaluation
with open('kb_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 256  # Adjust based on your available memory

# Define a function to process images in chunks
def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Base configuration
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"
bnb_quantization_config = BnbQuantizationConfig(load_in_8bit=True)

# Iterate over the 10 models
for i in range(1, 10):  # Assuming you have 19 finetuned models
    dir = f"./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain{i}"
    print(f"Evaluating with model from {dir}...")
    
    # Load and quantize model
    with init_empty_weights():
        empty_model = AutoModelForZeroShotImageClassification.from_config(AutoConfig.from_pretrained(repo_id))

    # Load the model from the directory
    weights_location = f"{dir}/model.safetensors"
    quantized_model = load_and_quantize_model(empty_model, weights_location=weights_location, bnb_quantization_config=bnb_quantization_config, device_map="auto")

    # Initialize tokenizer and processor
    tokenizer = AutoTokenizer.from_pretrained(repo_id)
    image_processor = AutoImageProcessor.from_pretrained(repo_id)
    
    # Initialize the pipeline without the device argument
    clip_pipeline = pipeline(
        model=quantized_model,
        task="zero-shot-image-classification",
        tokenizer=tokenizer,
        image_processor=image_processor,
        config=AutoConfig.from_pretrained(repo_id),
        model_kwargs={"load_in_8bit": True}
    )

    all_predictions = []
    all_true_labels = []

        # Process images in chunks and evaluate
    for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
        batch_images = []
        valid_labels = []
        for path, label in zip(batch_paths, batch_labels):
            try:
                # Open image and append to batch_images
                with Image.open(path) as img:
                    batch_images.append(img.convert("RGB"))
                valid_labels.append(label)
            except (FileNotFoundError, UnidentifiedImageError):
                # Skip images that cannot be opened
                continue

        # Get predictions for the batch of images
        try:
            predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
            predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction
            all_predictions.extend(predicted_labels)
            all_true_labels.extend(valid_labels)
        except Exception as e:
            print(f"An error occurred during prediction: {e}")
            continue

    # Calculate the accuracy for the current model
    correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
    accuracy = correct_predictions / len(all_true_labels) if all_true_labels else 0
    print(f"Accuracy for model {i}: {accuracy * 100:.2f}%\n")



Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain1...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 1: 97.07%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain2...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 2: 96.94%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain3...


...

Accuracy for model 7: 96.01%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain8...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 8: 96.01%

Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain9...


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 9: 95.74%



# quantize 4 bit

In [24]:

from accelerate.utils import BnbQuantizationConfig
bnb_quantization_config = BnbQuantizationConfig(load_in_8bit=True)
from accelerate.utils import load_and_quantize_model
from transformers import CLIPProcessor, CLIPModel, AutoModel
from accelerate import init_empty_weights
from transformers import AutoTokenizer, AutoConfig, AutoModel,AutoModelForZeroShotImageClassification
config = AutoConfig.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
with init_empty_weights():
    empty_model = AutoModelForZeroShotImageClassification.from_config(config)
    #CLIP(config=AutoConfig.from_pretrained("openai/clip-vit-large-patch14"))

# Move the model to GPU 0
print(empty_model.device)
model = AutoModel.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
from huggingface_hub import snapshot_download
weights_location = snapshot_download(repo_id="laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
quantized_model = load_and_quantize_model(empty_model, weights_location=weights_location, 
                                          bnb_quantization_config=bnb_quantization_config, device_map = "auto")



meta


Fetching 14 files:   0%|          | 0/14 [00:00<?, ?it/s]

In [26]:
from accelerate.utils import BnbQuantizationConfig
bnb_quantization_config = BnbQuantizationConfig(load_in_8bit=True)
from accelerate.utils import load_and_quantize_model
from transformers import CLIPProcessor, CLIPModel, AutoModelForCausalLM
from accelerate import init_empty_weights
from transformers import AutoTokenizer, AutoConfig, AutoModel,AutoModelForZeroShotImageClassification
tokenizer = AutoTokenizer.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
model = AutoModelForCausalLM.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K", device_map="auto", load_in_4bit=True)

ValueError: Unrecognized configuration class <class 'transformers.models.clip.configuration_clip.CLIPConfig'> for this kind of AutoModel: AutoModelForCausalLM.
Model type should be one of BartConfig, BertConfig, BertGenerationConfig, BigBirdConfig, BigBirdPegasusConfig, BioGptConfig, BlenderbotConfig, BlenderbotSmallConfig, BloomConfig, CamembertConfig, LlamaConfig, CodeGenConfig, CpmAntConfig, CTRLConfig, Data2VecTextConfig, ElectraConfig, ErnieConfig, FalconConfig, FuyuConfig, GitConfig, GPT2Config, GPT2Config, GPTBigCodeConfig, GPTNeoConfig, GPTNeoXConfig, GPTNeoXJapaneseConfig, GPTJConfig, LlamaConfig, MarianConfig, MBartConfig, MegaConfig, MegatronBertConfig, MistralConfig, MixtralConfig, MptConfig, MusicgenConfig, MvpConfig, OpenLlamaConfig, OpenAIGPTConfig, OPTConfig, PegasusConfig, PersimmonConfig, PhiConfig, PLBartConfig, ProphetNetConfig, QDQBertConfig, Qwen2Config, ReformerConfig, RemBertConfig, RobertaConfig, RobertaPreLayerNormConfig, RoCBertConfig, RoFormerConfig, RwkvCon

In [12]:
#original model
from accelerate.utils import BnbQuantizationConfig
from accelerate.utils import load_and_quantize_model
from transformers import CLIPProcessor, CLIPModel, AutoModel
from accelerate import init_empty_weights
from transformers import AutoTokenizer, AutoConfig, AutoModel,AutoModelForZeroShotImageClassification
config = AutoConfig.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
with init_empty_weights():
    empty_model = AutoModelForZeroShotImageClassification.from_config(config)
    #CLIP(config=AutoConfig.from_pretrained("openai/clip-vit-large-patch14"))

# Move the model to GPU 0
print(empty_model.device)
model = AutoModel.from_pretrained("laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
from huggingface_hub import snapshot_download
weights_location = snapshot_download(repo_id="laion/CLIP-ViT-B-32-laion2B-s34B-b79K")
quantized_model = load_and_quantize_model(empty_model, weights_location=weights_location, 
                                          bnb_quantization_config=bnb_quantization_config, device_map = "auto")

import os
import csv
from transformers import CLIPProcessor, CLIPModel, pipeline, CLIPImageProcessor
from PIL import Image
from transformers import AutoTokenizer, AutoConfig, AutoModel,AutoImageProcessor
import matplotlib.pyplot as plt
import time
import json

# Load the JSON data
with open('val_random.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

repo_id =  "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"

image_processor = AutoImageProcessor.from_pretrained(
    repo_id
)
tokenizer = AutoTokenizer.from_pretrained(repo_id, 
                                          config=AutoConfig.from_pretrained(repo_id))
model = quantized_model
clip_pipeline = pipeline(model=model,task="zero-shot-image-classification", tokenizer=tokenizer,
                    image_processor=image_processor, config=AutoConfig.from_pretrained(repo_id),
                        device_map="auto", model_kwargs={"load_in_8bit": True})

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

BATCH_SIZE = 256  # Adjust based on your available memory

all_predictions = []
all_true_labels = []
time_eval = []

for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
    batch_images = []
    valid_labels = []
    for path, label in zip(batch_paths, batch_labels):
        try:
            batch_images.append(Image.open(path))
            valid_labels.append(label)
        except (FileNotFoundError, UnidentifiedImageError):
            continue  # Skip images that cannot be opened

    # Get predictions for the batch of images
    predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
    predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

    all_predictions.extend(predicted_labels)
    all_true_labels.extend(valid_labels)

correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
accuracy = correct_predictions / len(all_true_labels)
print(f"Accuracy for model {i}: {accuracy * 100:.2f}%\n")


meta


Fetching 14 files:   0%|          | 0/14 [00:00<?, ?it/s]

Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model 9: 88.67%



In [22]:
from accelerate.utils import BnbQuantizationConfig, load_and_quantize_model
from transformers import CLIPProcessor, CLIPModel, AutoTokenizer, AutoConfig, AutoModelForZeroShotImageClassification, pipeline, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import json

# Load the JSON data for evaluation
with open('val_random.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 256  # Adjust based on your available memory

# Define a function to process images in chunks
def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

# Base configuration
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"

# Iterate over the 10 models
for i in range(1, 10):  # Assuming you have 19 finetuned models
    dir = f"./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain{i}"
    print(f"Evaluating with model from {dir}...")
    
    # Load and quantize model
    with init_empty_weights():
        empty_model = AutoModelForZeroShotImageClassification.from_config(AutoConfig.from_pretrained(repo_id))

    # Load the model from the directory
    weights_location = f"{dir}/model.safetensors"
    quantized_model = load_and_quantize_model(empty_model, weights_location=weights_location, bnb_quantization_config=bnb_quantization_config, device_map="auto")

    # Initialize tokenizer and processor
    tokenizer = AutoTokenizer.from_pretrained(repo_id)
    image_processor = AutoImageProcessor.from_pretrained(repo_id)
    
    # Initialize the pipeline without the device argument
    clip_pipeline = pipeline(
        model=quantized_model,
        task="zero-shot-image-classification",
        tokenizer=tokenizer,
        image_processor=image_processor,
        config=AutoConfig.from_pretrained(repo_id),
        model_kwargs={"load_in_8bit": True}
    )

    all_predictions = []
    all_true_labels = []

        # Process images in chunks and evaluate
    for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
        batch_images = []
        valid_labels = []
        for path, label in zip(batch_paths, batch_labels):
            try:
                # Open image and append to batch_images
                with Image.open(path) as img:
                    batch_images.append(img.convert("RGB"))
                valid_labels.append(label)
            except (FileNotFoundError, UnidentifiedImageError):
                # Skip images that cannot be opened
                continue

        # Get predictions for the batch of images
        try:
            predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
            predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction
            all_predictions.extend(predicted_labels)
            all_true_labels.extend(valid_labels)
        except Exception as e:
            print(f"An error occurred during prediction: {e}")
            continue

    # Calculate the accuracy for the current model
    correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
    accuracy = correct_predictions / len(all_true_labels) if all_true_labels else 0
    print(f"Accuracy for model {i}: {accuracy * 100:.2f}%\n")



Evaluating with model from ./workspace/output/laion-finetuned_v5e7_epoch10_random80_vtrain1...


NotImplementedError: Cannot copy out of meta tensor; no data!

# Efficiency comparison

In [1]:
import pandas as pd
from collections import Counter
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import torch
import torch.profiler

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

def calculate_category_accuracy(true_labels, predicted_labels):
    """Calculate the accuracy for each category and return it as a dictionary."""
    accuracies = {}
    true_labels_counter = Counter(true_labels)
    correct_predictions_counter = Counter([true for true, pred in zip(true_labels, predicted_labels) if true == pred])
    
    for label in true_labels_counter:
        accuracy = (correct_predictions_counter[label] / true_labels_counter[label]) if label in correct_predictions_counter else 0
        accuracies[label] = accuracy
    
    return accuracies

# Load the JSON data
with open('kb_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 1024  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"

image_processor = AutoImageProcessor.from_pretrained(repo_id)
tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
model = AutoModel.from_pretrained(repo_id).cuda()
clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                         device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(repo_id))

all_predictions = []
all_true_labels = []

def trace_handler(profiler):
    print("Trace handler called")
    try:
        print(profiler.key_averages().table(sort_by="cpu_time_total", row_limit=10))
        profiler.export_chrome_trace("trace.json")
    except Exception as e:
        print(f"Error in trace handler: {str(e)}")
# Start profiling
with torch.profiler.profile(
    activities=[torch.profiler.ProfilerActivity.CPU, torch.profiler.ProfilerActivity.CUDA],
    schedule=torch.profiler.schedule(wait=1, warmup=1, active=3),
    on_trace_ready=trace_handler,
    record_shapes=True,
    profile_memory=True,
    with_stack=True
) as profiler:
    for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
        batch_images = []
        valid_labels = []
        for path, label in zip(batch_paths, batch_labels):
            try:
                batch_images.append(Image.open(path).convert('RGB'))
                valid_labels.append(label)
            except (FileNotFoundError, UnidentifiedImageError):
                print(f"Skipping file: {path}, unable to open or not found.")
                continue  # Skip images that cannot be opened

        if batch_images:  # Ensure there are images to predict
            predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
            predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

            all_predictions.extend(predicted_labels)
            all_true_labels.extend(valid_labels)

        profiler.step()  # Advance the profiler

# Calculate and print overall accuracy
correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
accuracy = correct_predictions / len(all_true_labels) if all_true_labels else 0
print(f"Accuracy for model org: {accuracy * 100:.2f}%\n")

# Calculate and print category accuracies
category_accuracies = calculate_category_accuracy(all_true_labels, all_predictions)
print("Accuracy for each category:")
for category, accuracy in category_accuracies.items():
    print(f"{category}: {accuracy:.2f}")

# Convert the dictionary to a DataFrame
category_accuracy_df = pd.DataFrame(list(category_accuracies.items()), columns=['Category', 'Accuracy'])

print(category_accuracy_df)


Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.


Accuracy for model org: 73.67%

Accuracy for each category:
a photo of standard bathroom: 0.92
a photo of standard kitchen: 0.98
a photo of contemporary bathroom: 0.52
a photo of contemporary kitchen: 0.39
                           Category  Accuracy
0      a photo of standard bathroom  0.920690
1       a photo of standard kitchen  0.980892
2  a photo of contemporary bathroom  0.516949
3   a photo of contemporary kitchen  0.385027


STAGE:2024-04-22 17:39:10 514141:514141 ActivityProfilerController.cpp:311] Completed Stage: Warm Up
STAGE:2024-04-22 17:39:10 514141:514141 ActivityProfilerController.cpp:317] Completed Stage: Collection
STAGE:2024-04-22 17:39:10 514141:514141 ActivityProfilerController.cpp:321] Completed Stage: Post Processing


In [ ]:
import pandas as pd
from collections import Counter
import os
import json
from transformers import pipeline, AutoTokenizer, AutoConfig, AutoModel, AutoImageProcessor
from PIL import Image, UnidentifiedImageError
import torch
import torch.profiler

def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

def calculate_category_accuracy(true_labels, predicted_labels):
    """Calculate the accuracy for each category and return it as a dictionary."""
    accuracies = {}
    true_labels_counter = Counter(true_labels)
    correct_predictions_counter = Counter([true for true, pred in zip(true_labels, predicted_labels) if true == pred])
    
    for label in true_labels_counter:
        accuracy = (correct_predictions_counter[label] / true_labels_counter[label]) if label in correct_predictions_counter else 0
        accuracies[label] = accuracy
    
    return accuracies

# Load the JSON data
with open('kb_val.json', 'r') as f:
    data = [json.loads(line) for line in f]

# Extract image paths and labels
image_paths = [item['image'] for item in data]
labels = [item['caption'] for item in data]

BATCH_SIZE = 1024  # Adjust based on your available memory
repo_id = "laion/CLIP-ViT-B-32-laion2B-s34B-b79K"
model_dir = f"./workspace/output/backup_ckpts/laion-finetuned_v5e7_epoch10_fold1_threshold3"

image_processor = AutoImageProcessor.from_pretrained(repo_id)
tokenizer = AutoTokenizer.from_pretrained(repo_id, config=AutoConfig.from_pretrained(repo_id))
model = AutoModel.from_pretrained(model_dir).cuda()
clip_pipeline = pipeline(model=model, task="zero-shot-image-classification", tokenizer=tokenizer,
                         device=1, image_processor=image_processor, config=AutoConfig.from_pretrained(model_dir))

all_predictions = []
all_true_labels = []

def trace_handler(profiler):
    print("Trace handler called")
    try:
        print(profiler.key_averages().table(sort_by="cpu_time_total", row_limit=10))
        profiler.export_chrome_trace("trace.json")
    except Exception as e:
        print(f"Error in trace handler: {str(e)}")
# Start profiling
with torch.profiler.profile(
    activities=[torch.profiler.ProfilerActivity.CPU, torch.profiler.ProfilerActivity.CUDA],
    schedule=torch.profiler.schedule(wait=1, warmup=1, active=3),
    on_trace_ready=trace_handler,
    record_shapes=True,
    profile_memory=True,
    with_stack=True
) as profiler:
    for batch_paths, batch_labels in zip(chunks(image_paths, BATCH_SIZE), chunks(labels, BATCH_SIZE)):
        batch_images = []
        valid_labels = []
        for path, label in zip(batch_paths, batch_labels):
            try:
                batch_images.append(Image.open(path).convert('RGB'))
                valid_labels.append(label)
            except (FileNotFoundError, UnidentifiedImageError):
                print(f"Skipping file: {path}, unable to open or not found.")
                continue  # Skip images that cannot be opened

        if batch_images:  # Ensure there are images to predict
            predictions = clip_pipeline(images=batch_images, candidate_labels=valid_labels)
            predicted_labels = [pred[0]['label'] for pred in predictions]  # Top prediction

            all_predictions.extend(predicted_labels)
            all_true_labels.extend(valid_labels)

        profiler.step()  # Advance the profiler

# Calculate and print overall accuracy
correct_predictions = sum([true == pred for true, pred in zip(all_true_labels, all_predictions)])
accuracy = correct_predictions / len(all_true_labels) if all_true_labels else 0
print(f"Accuracy for model org: {accuracy * 100:.2f}%\n")

# Calculate and print category accuracies
category_accuracies = calculate_category_accuracy(all_true_labels, all_predictions)
print("Accuracy for each category:")
for category, accuracy in category_accuracies.items():
    print(f"{category}: {accuracy:.2f}")

# Convert the dictionary to a DataFrame
category_accuracy_df = pd.DataFrame(list(category_accuracies.items()), columns=['Category', 'Accuracy'])

print(category_accuracy_df)
